# **P1 - Transcriptómica II 2025**

This Google Colab notebook (R) demonstrates the analysis of a ~1000 PBMCs dataset available from 10X Genomics. We are starting with the filtered counts, where putative cells were previously distinguished from empty drops.

**1. Install packages**

In [ ]:
install.packages("Seurat", quietly=TRUE)

In [ ]:
## Bioconductor

if (!require("BiocManager", quietly = TRUE))
    install.packages("BiocManager")

#BiocManager::install("SingleR", quietly=TRUE, ask=FALSE, update=FALSE)
#BiocManager::install("celldex", quietly=TRUE, ask=FALSE, update=FALSE)
BiocManager::install("glmGamPoi", quietly=TRUE, ask=FALSE, update=FALSE)

In [ ]:
system("pip3 install leidenalg")

In [ ]:
install.packages('devtools')
devtools::install_github('immunogenomics/presto')

In [ ]:
library(tidyverse) #preinstalled in Google Colab
library(Seurat)
#library(SingleR)
#library(celldex)
library(patchwork)

In [ ]:
#added to make the axis labels and titles and legend titles larger in Google Colab
theme(axis.text = element_text(size = 12),
      axis.title = element_text(size = 14),
      legend.title = element_text(size = 14))

**2. Create Seurat object**

Load the filtered data matrix using the Read10X function from the Seurat package.

In [ ]:
#Load filtered expression data
datadir <- 'counts_filtered'
list.files(datadir)

expression_matrix <- Read10X(
  datadir,
  gene.column = 2,
  cell.column = 1,
  unique.features = TRUE,
  strip.suffix = FALSE
)

expression_matrix[1:5,1:5]
dim(expression_matrix)



In [ ]:
#Create seurat object
pbmc.seu <- CreateSeuratObject(counts = expression_matrix, min.cells = 3)
pbmc.seu

This is the initial Seurat object. It already contains *raw* counts in the RNA assay, a `meta.data` table with per-cell QC metrics, and an `active.ident`. This shows how to inspect assays, slots, and dimensions.

In [ ]:
# Basic slots
DefaultAssay(pbmc.seu)
Assays(pbmc.seu)
# see default layer
DefaultLayer(pbmc.seu[["RNA"]])  ##counts or data if normalized
colnames(pbmc.seu@meta.data)   # colnames(pbmc.seu@meta.data)[1:10]
dim(pbmc.seu)              # genes x cells
head(pbmc.seu@meta.data,2)

Seurat stores *raw* UMI counts in the `counts` slot and *normalized* values in the `data` slot. After `NormalizeData()`, the `data` slot holds log-normalized expression. The normalization does not overwrite the raw counts. This is similar for `SCTransform` although a new assay `SCT` is generated.

In [ ]:
# Raw counts (UMI)
raw_counts <- GetAssayData(pbmc.seu, assay = "RNA", layer = "counts")
##x_norm   <- GetAssayData(seu, assay="RNA", layer="data")["GeneA", ]

In [ ]:
##################
#### FUNCTION ####
##################

#' Plot scatter plot side by side with density
#'
#' A way to mitigate overplotting, which makes it difficult to see the density
#' of points on a plot even with translucent points.
#'
#' @parem seu Seurat object.
#' @param features Character vector of length 2 for the columns in the meta.data
#' slot to be plotted.
#' @param size Point size for scatter plot.
#' @param alpha Point opacity for scatter plot.
#' @param bins Numbers of bins for density plot.
#' @param log Whether to plot x and/or y axis on log scale.
#' @param xlab Label of x axis for both plots.
#' @param ylab Label of y axis for both plots.
#' @return Two ggplots patched together by \code{patchwork}.
plot_scatter_density <- function(seu, features, size = 0.5, alpha = 0.1,
                                 bins = 100, log = c("xy", "x", "y", "none"),
                                 xlab = NULL, ylab = NULL) {
  log <- match.arg(log)
  features <- intersect(features, names(seu@meta.data))
  if (length(features) < 2) {
    stop("Need 2 features to plot.")
  }
  if (length(features) > 2) {
    features <- features[1:2]
    warning("The first two elements of features are used.")
  }
  p <- ggplot(seu@meta.data, aes_string(features[1], features[2]))
  if (!is.null(xlab)) p <- p + xlab(xlab)
  if (!is.null(ylab)) p <- p + ylab(ylab)
  p <- switch(
    log,
    xy = p + scale_x_log10() + scale_y_log10() + annotation_logticks(),
    x = p + scale_x_log10() + annotation_logticks(sides = "b"),
    y = p + scale_y_log10() + annotation_logticks(sides = "l"),
    none = p
  )
  p1 <- p +
  geom_point(size = size, alpha = alpha)
  p2 <- p +
    geom_bin2d(bins = bins) +
    scale_fill_distiller(palette = "Blues", direction = 1)
  p1 + p2
}

**3. QC: Library Saturation**

Can we detect more genes by increasing sequencing depth?

In [ ]:
options(repr.plot.width=11, repr.plot.height=6)

plot_scatter_density(pbmc.seu, c("nCount_RNA", "nFeature_RNA"),
                     xlab = "Number of UMI per cell",
                     ylab = "Number of genes per cell")

There are a few cells with very high counts, which might be **doublets**. This is not a formal test for whether a droplet has a doublet. There are packages like `DoubletFinder` for this. Seurat objects can be subsetted just like matrices, and here cells with more than 20,000 total UMIs are removed.

This is a simplified version of the previous plots.

In [ ]:
ggplot(pbmc.seu@meta.data, aes(nCount_RNA, nFeature_RNA)) +
  geom_point(alpha = 0.7, size = 0.5) +
  labs(x = "Total UMI counts per cell", y = "Number of genes detected")

Potential things to look for in the type of QA plot produced above:
1. Data points in the bottom LEFT hand quadrant = low genes and UMIs per cell. May represent poor quality cells.
2. Data points in the bottom RIGHT hand quadrant = low genes but high UMIs per cell. These could be dying cells, but also could represent a population of a low complexity celltype (i.e red blood cells).

**4. QC: Percentage of Mitochondrial Counts**

Cells with high percentage of mitochondrial counts are usually deemed low quality and removed because when a cell bursts during sample preparation, transcripts in the cytoplasm are more easily lost than mitochondrially encoded transcripts, which are protected by the double membrane of mitochondria.

The Seurat function PercentageFeatureSet calculates the percentage of UMI counts in each cell that are attributed to certain genes, which can be genes with symbols that fit a certain pattern, such as beginning with MT- for human mitochondrially encoded genes. The ^ in the ^MT- anchors the "MT-" to the beginning of the string, so things like "fooMT-" will not be selected.

In [ ]:
pbmc.seu$pct_mt <- PercentageFeatureSet(pbmc.seu, pattern = "^MT-")  #"^mt-" for mouse

head(pbmc.seu@meta.data,2)

In [ ]:

plot_scatter_density(pbmc.seu, features = c("nCount_RNA", "pct_mt"),
                     log = "x", xlab = "Number of UMI per cell",
                     ylab = "Percentage of mitochondrial counts")

Sort of arbitrary; 20% seems like a good cutoff based on this plot.

PercentageFeatureSet can also calculate the percentage of UMIs attributed to a vector of genes, like here the marker genes of red blood cells (cell containing hemoglobin).

In [ ]:
pbmc.seu$pct_hb <- PercentageFeatureSet(pbmc.seu, pattern = "^HB")
plot_scatter_density(pbmc.seu, features = c("nCount_RNA", "pct_hb"),
                     log = "x", alpha = 0.3,
                     xlab = "Number of UMI per cell", ylab = "Percentage of hemoglobin count")

Violin plots are also very useful to see the distribution of detected genes (features), UMIs (counts=total molecules), percentage of mitochondrial genes, etc.

In [ ]:
options(repr.plot.width=9, repr.plot.height=9)

VlnPlot(pbmc.seu, c("nCount_RNA", "nFeature_RNA", "pct_mt", "pct_hb"), ncol=2, pt.size = 0.1)

**5. QC: Filtering low quality cells**

NOTE: you need to be careful when setting cut-offs that you're not losing unique cell populations

In [ ]:
# Filter your data
pbmc.seu <- subset(pbmc.seu, subset =
                           nCount_RNA < 20000 &
                           nCount_RNA > 1000 &
                           nFeature_RNA > 500 &
                           pct_mt < 20 &
                           pct_hb < 0.2)


How many cells are there left?

In [ ]:
pbmc.seu

How are total UMI counts and number of genes detected in each cell distributed after removing low quality cells?

In [ ]:
VlnPlot(pbmc.seu, c("nCount_RNA", "nFeature_RNA"), pt.size = 0.1)

**6. Exploratory data analysis**

`SCTransform` is used to normalize and scale data and find highly variable genes. This can replace `NormalizeData() %>% ScaleData() %>% FindVariableFeatures()`. This gives off warnings of maximum number of iterations reached, which do not seem to negatively affect results, so are suppressed by suppressWarnings.

*It is standard practice to apply a linear transformation ('scaling') before PCA. For single cell data this includes:*
*# 1. Shifting the expression of each gene, so that the mean expression across cells is 0*
*# 2. Scaling the expression of each gene, so that the variance across cells is 1*
*This gives equal weight in downstream analyses, so that highly-expressed genes do not dominate.*


In [ ]:
pbmc.seu <- suppressWarnings(SCTransform(pbmc.seu, verbose = FALSE))

In [ ]:
DefaultAssay(pbmc.seu)
Assays(pbmc.seu)
# see default layer
DefaultLayer(pbmc.seu[["RNA"]])  ##counts or data if normalized
DefaultLayer(pbmc.seu[["SCT"]])
colnames(pbmc.seu@meta.data)   # colnames(pbmc.seu@meta.data)[1:10]
dim(pbmc.seu)              # genes x cells
head(pbmc.seu@meta.data,2)

How many genes are stored in `data`? Why? How many genes are stored in `VariableFeatures`? Why?

In [ ]:
dim(GetAssayData(pbmc.seu, assay="RNA", layer="counts"))
dim(GetAssayData(pbmc.seu, assay="SCT", layer="data"))

In [ ]:
head(VariableFeatures(pbmc.seu))
length(VariableFeatures(pbmc.seu))

Remember that this dataset has over 25,000 genes detected. However, because genes are often co-regulated, the de facto dimensionality of the dataset is much lower. But how to find the effective lower dimensions? Furthermore, we can't visualize 25,000 dimensions and we need to project the data into 2 or 3 dimensions to get a visual sense of its structures. Here comes dimension reduction.

**Principal component analysis** (PCA) is a commonly used dimension reduction method. It tries to find the hyperplane (just like a 2D plane, but generalized to higher dimensions) that most closely fits the data. On each dimension, it maximizes the variance of the data projected on this dimension, and for the next dimension, it again maximizes variance of the data projected on the dimension given that this dimension is perpendicular to the previous dimension, so in the end, all such dimensions are perpendicular to each other. The first such dimensions, called principal components (PC), is the PC that explains more variance than any other PC. PCs are ranked by how much variance they explain. The later PCs capture less variance, which might have come from noise. Typically a small number of dimensions are calculated, like 20 or 30, to keep the more "relevant" variance and remove noise on the one hand, and to speed up downstream computations on the other hand.

There are many other methods for dimension reduction as well, such as tSNE and UMAP, which will be used below for visualization in 2D. There are dimension reduction methods that have different objectives, sometimes used in place of PCA, such as independent component analysis (ICA), which maximizes what deviates from the normal distribution such as bimodality and skew on each dimension, canonical component analysis (CCA), which maximizes correlation between two datasets on each dimension and is one step in Seurat's data integration, and non-negative matrix factorization (NMF), which ensures that the projections are non-negative. More recently, with the development of neuronetworks, variational autoencoders can be used for dimension reduction in place of PCA.

How many PCs to use? It's actually not all that easy to tell. A common and easy way is to plot how much variance/standard deviation is explained by each PC and find the "elbow" of this plot. Usually for this kind of data, the first few PCs explain a lot of variance, and then it plateaus. The PC where variance explains starts to plateau, called the elbow point, is the number of PCs used for downstream analysis. There are other methods to decide how many PCs to use as well, such as JackStraw in Seurat.

Here 40 PCs are computed and their variance explained plotted (actually standard deviation here). The elbow is at around PC 10, but just to be safe and not to throw away too much information, we'll use 20 PCs.

In [ ]:
pbmc.seu <- RunPCA(pbmc.seu, npcs = 40, verbose = FALSE)
ElbowPlot(pbmc.seu, 40)

What does the data look like when projected to the first 2 PCs?

In [ ]:
PCAPlot(pbmc.seu)

Each PC is actually a linear combination of genes, which are the original dimensions. Which genes are contributing the most to the top PCs?

In [ ]:
options(repr.plot.width=12, repr.plot.height=10)
VizDimLoadings(pbmc.seu, ncol = 3)

Here the cells and genes with extreme PCA scores are plotted and the color is gene expression in each cell of interest. The 500 cells with the most extreme PCA scores are selected for each PC to speed up the code.

In [ ]:
options(repr.plot.width=9, repr.plot.height=9)
DimHeatmap(pbmc.seu, dims = 1:6, ncol = 3, cells = 500, balanced = TRUE)

**7. Leiden clustering**

How many different types of cells are there in this dataset? How many cells are there in each type? Immunologists probably can already make out some cell types from the previous two plots, but we can get a sense of how many types of cells by clustering. There're many different methods of clustering, such as Leiden, Louvain, smart local moving (SLM), k-means, and walk trap. The one used here is Leiden, which is a more refined version of Louvain, which maximizes modularity by placing cells into the cluster of some  k  nearest neighbors and then clustering those clusters.

So first we need to find the  k  nearest neighbors of each cell, which is done by `FindNeighbors`, with default  k=20 . Generally, increasing  k , in the argument k.param, decreases the number of clusters. The argument dims = 1:20 means PCs 1 through 20 are used to build the  k  nearest neighbor graph. Then `FindClusters`, does clustering with specified algorithm (algorithms 1 and 2 are variants of Louvain, 3 is SLM, annd 4 is Leiden). The larger resolution parameter, the finer the cluster are and the larger the number of clusters. The default setting is resolution = 0.8, but here it's set to 0.5 to make the clusters less finer.

In [ ]:
pbmc.seu <- FindNeighbors(pbmc.seu, reduction="pca", dims = 1:20, k.param=40, verbose = FALSE)
pbmc.seu <- suppressWarnings(FindClusters(pbmc.seu, algorithm = 4, verbose = FALSE, resolution = 0.5))

pbmc.seu

In [ ]:
head(pbmc.seu@meta.data)

In [ ]:
table(pbmc.seu@meta.data$seurat_clusters)

**8. t-SNE**

In PCA, it can be hard to separate clusters from each other in the projection into two PCs; separation of some clusters may only be captured by other PCs, making visualization hard. A way to project everything into two or three dimensions for visualization while preserving local structures of the data is t-stochastic neighborhood embedding (tSNE), called by Seurat's RunTSNE function. Here tSNE is used to project the first 20 PCs to 2 dimensions for visualization. Now we see the clusters.

Note that tSNE does not preserve global structures well, so don't take distance in tSNE projections too seriously.

In [ ]:
options(repr.plot.width=9, repr.plot.height=6)

pbmc.seu <- RunTSNE(pbmc.seu, dims = 1:20)
TSNEPlot(pbmc.seu, label = TRUE, label.size = 6)

**9. UMAP**

An alternative to tSNE is uniform manifold approximation and projection (UMAP), which better preserves global structures.

In [ ]:
pbmc.seu <- RunUMAP(pbmc.seu, dims = 1:20, verbose = FALSE)
UMAPPlot(pbmc.seu, label = TRUE, label.size = 6)

Another way of plotting results:

In [ ]:
DimPlot(pbmc.seu, reduction = "umap", split.by = "orig.ident", label = TRUE)

PCA embeddings live in the `reductions` slot. After choosing the number of PCs, we run UMAP, construct an SNN graph, and call clusters. All these objects—PCA, UMAP, neighbors, clusters—are stored back into the Seurat object.

In [ ]:
# Reductions present:
Reductions(pbmc.seu)
head(Embeddings(pbmc.seu, "umap"))

**10. Find cluster-specific genes (differential expression)**

What types of cells are there in those clusters? One of the ways to answer this question is differential expression, i.e. to find which genes are differentially expressed between clusters. There're many different methods of DE, such as Wilcoxon rank sum test, which is the default in Seurat. Other methods provided by Seurat include Student's t test, area under the receiver operator curve, logistic regression likelihood ratio test, MAST, and DESeq2. Here we use the Wilcoxon method, which is the default in Seurat.


The Seurat function `FindAllMarkers` find genes that are more or less expressed within each cluster compared to all other cells. The `test.use` argument specifies whichc test is used for DE; `min.pct = 0.2` means only test genes detected in at least 20% of cells within the cluster; `min.diff.pct = 0.2` means the fraction of cells expressing the gene within the cluster and without must be at least 0.2 for the gene to be tested; `only.pos = TRUE` means only genes more expressed within the cluster are tested, but the default is FALSE so genes that are less expressed are also tested by default.

We'll start with `FindMarkers`, since it allows you to choose exactly which cluster you'd like to focus on.

In [ ]:
cluster1.markers <- FindMarkers(pbmc.seu, ident.1 = 1, min.pct = 0.2)
cluster1.markers$pct.diff <- cluster1.markers$pct.1 - cluster1.markers$pct.2
cluster1.markers.df <- as_tibble(cluster1.markers, rownames = "geneID")


In [ ]:
head(cluster1.markers.df)

In [ ]:
# plot genes of interest on UMAP
FeaturePlot(pbmc.seu,
            reduction = "umap",
            features = c("SERPINA1"),
            pt.size = 0.4,
            order = TRUE,
            #split.by = "orig.ident",
            min.cutoff = 'q10',
            label = FALSE)

Now, let's analyze all markers for all clusters. Then, plot the most differentially expressed (DE) genes of each cluster.

How to get the most significant DE gene for each cluster? Here `group_by` makes sure that the `top_n` operation is done separately within each cluster, not within the whole data frame. The function `top_n` picks the row of the data frame that has the smallest value in -p_val_adj, or the smallest p-value after correcting for multiple testing. Here the function `pull` gets the gene column from the resulting data frame, so `top_markers` is a vector of genes rather than a data frame.


In [ ]:
# now let's try with FindAllMarkers
pbmc.all.markers <- FindAllMarkers(pbmc.seu, only.pos = TRUE, min.pct = 0.20, logfc.threshold = 0.20)

In [ ]:
head(pbmc.all.markers)

In [ ]:
?top_n

In [ ]:
# let's take the top marker gene for each cluster and plot in the UMAP
top1 <- pbmc.all.markers %>%
  group_by(cluster) %>%
  top_n(n = 1, -p_val_adj) %>%
  pull(gene)

top1

In [ ]:
options(repr.plot.width=18, repr.plot.height=12)
FeaturePlot(pbmc.seu, top1, reduction = "umap")

While some top DE genes are specific to one cluster, some are shared by two or more, perhaps related clusters. See more DE genes for each cluster to get a better sense of cell types.

Plot violin plot for expression of each top DE gene within each cluster.

In [ ]:
?VlnPlot

In [ ]:
VlnPlot(pbmc.seu, top1, pt.size = 0.1, ncol = 2)

Here the 5 in `top_n` means getting the top 5 most significant DE genes in each cluster. Since some clusters share DE genes, such as when the clusters consist of similar but still somewhat different cells, `unique` drops the duplicates.

In [ ]:
# let's take the top 5 marker genes for each cluster and plot as a heatmap
top5 <- pbmc.all.markers %>%
  group_by(cluster) %>%
  top_n(n = 5, -p_val_adj) %>%
  pull(gene) %>% unique()
top5

In [ ]:
DoHeatmap(pbmc.seu, features = top5)

In [ ]:
options(repr.plot.width=9, repr.plot.height=14)
DotPlot(pbmc.seu, features = top5) +
  coord_flip()

`meta.data` is just a data frame indexed by cells—add whatever covariates you need. We can switch identities (`Idents`) to any metadata column, enabling quick stratified plots.

In [ ]:
head(Idents(pbmc.seu))

In [ ]:
head(pbmc.seu@meta.data,2)

**11. Raw vs normalized visualization**
Same genes, two slots: raw counts vs. SCTransformed values. This is intended to see the effect of normalization on dispersion and cluster separation.

In [ ]:
Idents(pbmc.seu) <- "seurat_clusters"
#genes.show <- head(VariableFeatures(pbmc.seu), 6)
genes.show <- top1
VlnPlot(pbmc.seu, features = genes.show, layer = "counts", pt.size = 0, ncol=2) + ggtitle("Raw counts")
VlnPlot(pbmc.seu, features = genes.show, layer = "data",   pt.size = 0, ncol=2) + ggtitle("SCT")

**12. Saving and slimming**
For reproducibility, always save the object after key stages. `DietSeurat()` produces a lighter version for sharing or archiving while keeping the essential analysis artifacts.

In [ ]:
# Save full object
saveRDS(pbmc.seu, "seu_full.rds")
#seu <- readRDS("seu_full.rds")

# Slim object for sharing: keep main slots only
seu.slim <- DietSeurat(
  pbmc.seu,
  layers = c("counts","data"), scale.data = FALSE,
  assays = c("RNA","SCT"), dimreducs = c("pca","umap"), graphs = TRUE
)
saveRDS(seu.slim, "seu_slim.rds")
#seu <- readRDS(seu_slim.rds)

**To install before taking the break!!!!!!!!!!!!!!!!!!!**

In [ ]:
BiocManager::install("SingleR", quietly=TRUE, ask=FALSE, update=FALSE)
BiocManager::install("celldex", quietly=TRUE, ask=FALSE, update=FALSE)
install.packages("viridis", quietly=TRUE)
install.packages("pheatmap", quietly=TRUE)

In [ ]:
library(SingleR)
library(celldex)
library(viridis)
library(pheatmap)

**13. Cell type annnotation**

There are well-known marker genes for many cell types, which can help us to annotate cell types for clusters. Besides, methods have been developed to use existing data with annotated cell types as references to annotate new datasets. Such methods include SingleR and CellAssign. Here we use some manual annotation and SingleR. For manual annotation, cell type-specific genes were retrieved from [CellMarker](http://xteam.xbio.top/CellMarker/).


*It can also be useful to turn the Seurat object into a* **singleCellExperiment** *object, for better interoperability with other bioconductor tools.*



In [ ]:
# Seurat allows you to convert directly to SingleCellExperiment object
pbmc.sce <- as.SingleCellExperiment(pbmc.seu)


In [ ]:
pbmc.sce

In [ ]:
# create a list of markers
# you can find cell specific markers here: http://biocc.hrbmu.edu.cn/CellMarker/
pbmc_marker_list <- list(
  Monocytes = c("CD14", "CD68"),
  `T cells` = c("CD2", "CD3D", "TRAC", "IL32", "CD3E", "PTPRC"),
  `NK cells` = c("GZMK", "KLRF1", "CCL3", "CMC1", "NKG7", "PTPRC"),
  `Plasma cells` = c("CD27", "IGHG1", "CD79A", "IGHG2", "PTPRC", "IGKC"),
  `Mature B cells` = c("MS4A1", "LTB", "CD52", "IGHD", "CD79A", "PTPRC", "IGKC"))


In [ ]:
options(repr.plot.width=18, repr.plot.height=12)
VlnPlot(pbmc.seu, pbmc_marker_list$`T cells`, pt.size = 0.1)

There exists a large collection of reference expression datasets with curated cell type labels for use with SingleR package.



In [ ]:
# a different way of labeling clusters using public datasets
# now label using singleR and celldex (requires an internet connection to connect to ExperimentHub)
#ENCODE.data <- BlueprintEncodeData(ensembl = FALSE) #259 RNA-seq samples of pure stroma and immune cells as generated and supplied by Blueprint and ENCODE
#HPCA.data <- HumanPrimaryCellAtlasData(ensembl = FALSE) #713 microarray samples from the Human Primary Cell Atlas (HPCA) (Mabbott et al., 2013).
#DICE.data <- DatabaseImmuneCellExpressionData(ensembl = FALSE) #1561 bulk RNA-seq samples of sorted immune cell populations
#ImmGen.data <- ImmGenData(ensembl = FALSE) # 830 microarray samples of pure mouse immune cells, generated by the Immunologic Genome Project (ImmGen)
Monaco.data <- MonacoImmuneData(ensembl = FALSE) #114 bulk RNA-seq samples of sorted immune cell populations that can be found in GSE107011.
#MouseRNAseq.data <- MouseRNAseqData(ensembl = FALSE) #358 bulk RNA-seq samples of sorted cell populations
#Hemato.data <- NovershternHematopoieticData(ensembl = FALSE) #211 bulk human microarray samples of sorted hematopoietic cell populations that can be found in GSE24759


In [ ]:
Monaco.data

In [ ]:
head(Monaco.data$label.main)
table(Monaco.data$label.main)

In [ ]:
head(Monaco.data$label.fine)
table(Monaco.data$label.fine)

**QUESTION**

1. What is celldex pckage for?
2. What is the meaning of `ensembl=FALSE`?
3. What was the level of the cell type annotation used in the practical? Explain.

In [ ]:
predictions <- SingleR(test=pbmc.sce, assay.type.test=1,
                       ref=Monaco.data, labels=Monaco.data$label.main)


In [ ]:
predictions

In [ ]:
plotScoreHeatmap(predictions)

In [ ]:
pbmc.seu


In [ ]:
#now add back to singleCellExperiment object (or Seurat objects)
#pbmc.sce[["SingleR.labels"]] <- predictions$labels
#plotUMAP(pbmc.sce, colour_by = "SingleR.labels")
all(rownames(pbmc.seu@meta.data[1:5,]) == rownames(predictions[1:5,]))
all(rownames(pbmc.seu@meta.data[1067:1072,]) == rownames(predictions[1067:1072,]))

pbmc.seu@meta.data$SingleR.labels <- predictions$labels



In [ ]:
options(repr.plot.width=14, repr.plot.height=6)
UMAPPlot(pbmc.seu, group.by = c("seurat_clusters","SingleR.labels"), label = TRUE, label.size = 6) + NoLegend()

**TASK**

As you may have noticed, B cells cluster doesn't look homogeneous. Can you further investigate if there are two B cells subclusters? Are mature B cells present in both subclusters? You can use the mature B cell markers defined above. TIP: use Seurat function `AddModuleScore` to calculate a "mature B cell score" per cell. Then visualize it with `FeaturePlot`. TIP: annotate with SingleR using the `fine` labels and inspect the new heatmap.